### Understanding the Effects of Anthropogenic Forces on Global Warming

In [ ]:
#install the following packages
# %pip install statsmodels plotly seaborn scikit-learn pmdarima
#pmdarima is a package that helps to find the best ARIMA model for time series data

In [1]:
# import packages needed for this project
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from scipy import stats
import sklearn
from sklearn import metrics
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import mean_squared_error
from sklearn.metrics import r2_score
from sklearn.model_selection import GridSearchCV
from statsmodels.tsa.arima.model import ARIMA
from statsmodels.graphics.tsaplots import plot_predict
# from statsmodels.tsa.arima_model import ARMA
from statsmodels.tsa.stattools import adfuller
from statsmodels.tsa.vector_ar.vecm import coint_johansen
from statsmodels.tsa.vector_ar.var_model import VAR
from statsmodels.tsa.vector_ar.vecm import VECM
import statsmodels.tsa.stattools as ts
from statsmodels.tsa.stattools import grangercausalitytests
import plotly
import statsmodels.api as sm
from pmdarima import model_selection
import pmdarima as pm
import prophet
from pandas.api.types import is_string_dtype
from pandas.api.types import is_numeric_dtype
%matplotlib inline
sm.tsa.statespace.SARIMAX
import warnings
warnings.filterwarnings('ignore')

In [2]:
import os
os.getcwd()

'c:\\Users\\musta\\Project_Temp\\data'

## Loading the Temperature data

The HadCRUT5 near surface temperature dataset used in this study consist of blended data from CRUTEM5 surface air temperature dataset and HadSST4 sea-surface temperature dataset.  
The time series are best estimates computed as means of regional time series computed for each of 200 ensemble member realisations. They are presented as temperature anomalies (deg C) relative to 1961 - 1990. More about the dataset can be found here:  https://www.metoffice.gov.uk/hadobs/hadcrut5/data/current/download.html  


In [32]:
#load the annual and monthly temperature data
temperature_annual_df = pd.read_csv('temperature/HadCRUT.5.0.1.0.analysis.summary_series.global.annual.csv')
temperature_monthly_df = pd.read_csv('temperature/HadCRUT.5.0.1.0.analysis.summary_series.global.monthly.csv')

In [33]:
#check for missing values 
print(f'Yearly data: The number of missing values in {[i for i in temperature_annual_df.columns]} are:\n {[i for i in temperature_annual_df.isnull().sum()]} respectively\n')
print(f'Monthly data: The number of missing values in {[i for i in temperature_monthly_df.columns]} are:\n {[i for i in temperature_monthly_df.isnull().sum()]} respectively')

Yearly data: The number of missing values in ['Time', 'Anomaly (deg C)', 'Lower confidence limit (2.5%)', 'Upper confidence limit (97.5%)'] are:
 [0, 0, 0, 0] respectively

Monthly data: The number of missing values in ['Time', 'Anomaly (deg C)', 'Lower confidence limit (2.5%)', 'Upper confidence limit (97.5%)'] are:
 [0, 0, 0, 0] respectively


In [34]:
#first 5 rows of the annual temperature data
temperature_annual_df.head()

Time  Anomaly (deg C)  Lower confidence limit (2.5%)  \
0  1850        -0.417659                      -0.589203   
1  1851        -0.233350                      -0.411868   
2  1852        -0.229399                      -0.409382   
3  1853        -0.270354                      -0.430009   
4  1854        -0.291630                      -0.432824   

   Upper confidence limit (97.5%)  
0                       -0.246115  
1                       -0.054832  
2                       -0.049416  
3                       -0.110700  
4                       -0.150436

In [35]:
#first 5 rows of the monthly temperature data
temperature_monthly_df.head()

Time  Anomaly (deg C)  Lower confidence limit (2.5%)  \
0  1850-01        -0.674564                      -0.981772   
1  1850-02        -0.333416                      -0.700901   
2  1850-03        -0.591323                      -0.933919   
3  1850-04        -0.588721                      -0.898259   
4  1850-05        -0.508185                      -0.761214   

   Upper confidence limit (97.5%)  
0                       -0.367357  
1                        0.034069  
2                       -0.248726  
3                       -0.279183  
4                       -0.255157

In [40]:
#change the time column to datetime for only year
temperature_annual_df['Date'] = pd.to_datetime(temperature_annual_df['Time'], format='%Y')
#rename the Time column to Year
temperature_annual_df = temperature_annual_df.rename(columns={'Time':'Year'})
#set the Date column as the index
temperature_annual_df.set_index('Date', inplace=True)
temperature_annual_df.head()

Year  Anomaly (deg C)  Lower confidence limit (2.5%)  \
Date                                                               
1850-01-01  1850        -0.417659                      -0.589203   
1851-01-01  1851        -0.233350                      -0.411868   
1852-01-01  1852        -0.229399                      -0.409382   
1853-01-01  1853        -0.270354                      -0.430009   
1854-01-01  1854        -0.291630                      -0.432824   

            Upper confidence limit (97.5%)  
Date                                        
1850-01-01                       -0.246115  
1851-01-01                       -0.054832  
1852-01-01                       -0.049416  
1853-01-01                       -0.110700  
1854-01-01                       -0.150436

In [43]:
#change the Time column of the monthly data to datetime and set it as the index
temperature_monthly_df['Date'] = pd.to_datetime(temperature_monthly_df['Time'])
temperature_monthly_df.set_index('Date', inplace=True)
temperature_monthly_df.head()

## Exploratory Data Analysis

In [46]:
#rename the Anomaly (deg C) column to Anomaly
temperature_annual_df = temperature_annual_df.rename(columns={'Anomaly (deg C)':'Anomaly'})
#select the column needed for the analysis
temperature_ann_df = temperature_annual_df[['Anomaly']]

In [95]:
#plot the monthly temperature anomaly
plt.figure(figsize=(12,6), dpi=1500)
plt.plot(temperature_monthly_df['Time'], temperature_monthly_df['Anomaly (deg C)'], color='purple', linewidth=1.5)
#for the x-asis to be readable, we will plot the x-axis every 10 years
plt.xticks(temperature_monthly_df['Time'][::120], rotation=90)
plt.title('Near Surface Temperature Anomaly (°C)', fontsize=20)
plt.xlabel('Month', fontsize=20, color='darkgreen')
plt.ylabel('Anomaly (°C)', fontsize=20, color='darkgreen')
plt.annotate('rapid growth since the 1950s', xy=('1960-01', 0.2), xytext=('1900-01', 0.6), color='darkgreen', fontsize=12, arrowprops=dict(facecolor='red'));
#plt.annotate('rapid growth since the 1950s', xy=('1960-01-01', 0.2), xytext=('1900-01-01', 0.6), color='darkgreen', fontsize=12, arrowprops=dict(facecolor='red'));


In [78]:
plt.figure(figsize=(12,6), dpi=1000)
plt.plot(temperature_annual_df['Year'], temperature_annual_df['Anomaly'], color='purple', linewidth=2)
plt.title('Near Surface Temperature Anomaly (°C)', fontsize=20)
plt.xlabel('Year', fontsize=20, color='darkgreen')
plt.ylabel('Anomaly (°C)', fontsize=20, color='darkgreen')   
# plt.annotate('Source: https://crudata.uea.ac.uk/cru/data/temperature/', (0,0), (-80,-40), fontsize=10, xycoords='axes fraction', textcoords='offset points', va='top')
plt.annotate('rapid growth since the 1950s', xy=(1960, 0.2), xytext=(1900, 0.6), 
             color='darkgreen', fontsize=12, arrowprops=dict(facecolor='red'));

<font color=darkgreen>**It is obvious from the above plot that there has been a rapid growth in temperature since the 1950s**<font>

## Carbon dioxide emissions data

In [103]:
co_2_df = pd.read_csv('co2/Monthly_co2/co2_brw_surface-insitu_1_ccgg_MonthlyData.txt', skiprows=157, sep='\s+', header=0)

In [107]:
co_2_df.head()

site_code  year  month  day  hour  minute  second              datetime  \
0       BRW  1973      8    1     0       0       0  1973-08-01T00:00:00Z   
1       BRW  1973      9    1     0       0       0  1973-09-01T00:00:00Z   
2       BRW  1973     10    1     0       0       0  1973-10-01T00:00:00Z   
3       BRW  1973     11    1     0       0       0  1973-11-01T00:00:00Z   
4       BRW  1973     12    1     0       0       0  1973-12-01T00:00:00Z   

   time_decimal  midpoint_time   value  value_std_dev  nvalue  latitude  \
0   1973.580822      114325200  322.73           0.84      23    71.323   
1   1973.665753      117003600  324.79           1.81      29    71.323   
2   1973.747945      119595600  329.86           2.78      29    71.323   
3   1973.832877      122274000  333.61           0.77      27    71.323   
4   1973.915068      124866000  334.60           1.60      30    71.323   

   longitude  altitude  elevation  intake_height qcflag  
0   -156.611      27.0       11.0           16.0    ...  
1   -156.611      27.0       11.0           16.0    ...  
2   -156.611      27.0       11.0           16.0    ...  
3   -156.611      27.0       11.0           16.0    ...  
4   -156.611      27.0       11.0           16.0    ...

In [108]:
co_2_df.columns

Index(['site_code', 'year', 'month', 'day', 'hour', 'minute', 'second',
       'datetime', 'time_decimal', 'midpoint_time', 'value', 'value_std_dev',
       'nvalue', 'latitude', 'longitude', 'altitude', 'elevation',
       'intake_height', 'qcflag'],
      dtype='object')

In [ ]:
#select the columns needed for the analysis: datetime and  value
co_2_df = co_2_df[['']]